In [1]:
import re
from nltk.stem import SnowballStemmer
from nltk.corpus import stopwords

stopwords = frozenset(stopwords.words("english") + [
 'ut', '\'re','.', ',', '--', '\'s', '?', ')', '(', ':', '\'',
 '\"', '-', '}', '{', '&', '|', 'rt', '', u'\u2014' ])

stemmer = SnowballStemmer("english")

tokenizer = re.compile(r"\w+")

JSON_FILENAME = "sample_west.json" 
EXCEL_FILENAME = "sample_west.xlsx"

In [2]:
import json


with open(JSON_FILENAME, "r") as file:
    sample = json.load(file)
    
sample

{'after': [{'_id': '5d625bc077a39fca2ded410f',
   'contributors': None,
   'coordinates': None,
   'created_at': '2019-08-25T09:58:19',
   'display_text_range': [50, 140],
   'entities': {'hashtags': [],
    'symbols': [],
    'urls': [{'display_url': 'twitter.com/i/web/status/1…',
      'expanded_url': 'https://twitter.com/i/web/status/1165564048953528321',
      'indices': [117, 140],
      'url': 'https://t.co/6YoEYDRrJB'}],
    'user_mentions': [{'id': 1157338850253049856,
      'id_str': '1157338850253049856',
      'indices': [0, 15],
      'name': 'Yorkshire Man in Lancashire',
      'screen_name': 'YorkshireTweet'},
     {'id': 1134728358,
      'id_str': '1134728358',
      'indices': [16, 29],
      'name': 'Jenny',
      'screen_name': 'queenbeeof90'},
     {'id': 14933304,
      'id_str': '14933304',
      'indices': [30, 40],
      'name': 'Jo Swinson',
      'screen_name': 'joswinson'},
     {'id': 5680622,
      'id_str': '5680622',
      'indices': [41, 49],
      'name

In [7]:
def getnicetext(r):
    try:
        text = r["extended_tweet"]["full_text"]
    except KeyError:
        try:
            text = r["text"][:getnicetext.regex.search(r["text"]).end()] + r["retweeted_status"]["extended_tweet"]["full_text"]
        except (KeyError, AttributeError):
            text = r["text"]

    return text

getnicetext.regex = re.compile(r"RT @[A-Za-z0-9_]{1,15}: ")

def analyze(statuses):
    climateWords = {'climat', 'chang', 'global', 'warm'}
    disastersWords = {'hurrican', 'earthquake', 'tornado', 'storm'}
    acceptWords = {'real', 'believ', 'deterior', 'grave', 'danger', 'ignor', 'warn', 'impact', 'extrem', 'resilien', 'sever'}
    denyWords = {'fake', 'hoax', 'deni', 'deny', 'doubt', 'scheme', 'scam'}
    posSentWords = {'hope', 'wish', 'best', 'pray', 'share', 'great', 'well', 'offer', 'resolv'}
    negSentWords = {'hate', 'stupid', 'offens', 'fear', 'fuck', 'crazi', 'shit', 'wast', 'disgrac', 'scold', 'anxieti'}
    
    for r in statuses:
        tags = set()
        words = [stemmer.stem(w).lower() for w in tokenizer.findall(getnicetext(r)) if w.lower() not in stopwords]
        
        for word in words:
            if word in climateWords:
                tags.add("climate")
                
            if word in disastersWords:
                tags.add("disaster")
                
            if word in acceptWords:
                tags.add("acceptance")
                
            if word in denyWords:
                tags.add("denial")
                
            if word in posSentWords:
                tags.add("positive")
                
            if word in negSentWords:
                tags.add("negative")
                
        r["tags"] = list(sorted(tags))

analyze(sample["before"])
analyze(sample["during"])
analyze(sample["after"])

In [14]:
import pandas as pd
import numpy as np
import datetime
import collections

def statusestodf(statuses):
    data = collections.OrderedDict([
        ("ID", []),
        ("Username", []),
        ("Timestamp", []),
        ("Text", []),
        ("Climate change?", []),
        ("Natural disaster?", []),
        ("Acceptance/Denial?", []),
        ("Positive/Negative?", [])
    ])
    
    for r in statuses:
        data["ID"].append(r["id_str"])
        data["Username"].append(r["user"]["screen_name"])
        data["Timestamp"].append(datetime.datetime.strptime(r["created_at"], "%Y-%m-%dT%H:%M:%S").replace(tzinfo = datetime.timezone.utc))
        data["Text"].append(getnicetext(r))
        
        data["Climate change?"].append("climate" in r["tags"])
        data["Natural disaster?"].append("disaster" in r["tags"])
        
        if "acceptance" in r["tags"] and "denial" in r["tags"]:
            belief = np.nan
        elif "acceptance" in r["tags"]:
            belief = "Acceptance"
        elif "denial" in r["tags"]:
            belief = "Denial"
        else:
            belief = np.nan
        
        if "positive" in r["tags"] and "negative" in r["tags"]:
            sentiment = np.nan
        elif "positive" in r["tags"]:
            sentiment = "Positive"
        elif "negative" in r["tags"]:
            sentiment = "Negative"
        else:
            sentiment = np.nan
            
        data["Acceptance/Denial?"].append(belief)
        data["Positive/Negative?"].append(sentiment)
    
    return pd.DataFrame(data)

before_df = statusestodf(sample["before"])
during_df = statusestodf(sample["during"])
after_df = statusestodf(sample["after"])

during_df

ID         Username                 Timestamp  \
0    1165564048953528321  PaulineMoorhou2 2019-08-25 09:58:19+00:00   
1    1165576661896531969  TheAndrewHorton 2019-08-25 10:48:26+00:00   
2    1166363282430660609    Stop_Solaroad 2019-08-27 14:54:11+00:00   
3    1167570630172168192          kaarrff 2019-08-30 22:51:45+00:00   
4    1167568849484619776  LeavesBandMates 2019-08-30 22:44:40+00:00   
5    1166812665882304512     honeydroppss 2019-08-28 20:39:52+00:00   
6    1166495239617597440           bln231 2019-08-27 23:38:32+00:00   
7    1165208588916334592        softyjmin 2019-08-24 10:25:50+00:00   
8    1167771313274064896        henry0410 2019-08-31 12:09:11+00:00   
9    1165137979565924354  MatheusBrunell3 2019-08-24 05:45:16+00:00   
10   1165828355511521280      PFortebuono 2019-08-26 03:28:34+00:00   
11   1167891628456996866       weertechum 2019-08-31 20:07:17+00:00   
12   1166857626715602944         heyyberv 2019-08-28 23:38:32+00:00   
13   1165688988616843265        jloveself 2019-08-25 18:14:46+00:00   
14   1167697689938710528       patriot462 2019-08-31 07:16:38+00:00   
15   1166780031441330177       myboxlimit 2019-08-28 18:30:11+00:00   
16   1166881015811362817      azardsphere 2019-08-29 01:11:28+00:00   
17   1165928422109077504    BarroneRobert 2019-08-26 10:06:12+00:00   
18   1166391691995009024  paulinearnoelia 2019-08-27 16:47:04+00:00   
19   1165177502689636353            tedhu 2019-08-24 08:22:19+00:00   
20   1165686611184689152     hayes_mcdole 2019-08-25 18:05:20+00:00   
21   1166664858110238722  Martamendoza718 2019-08-28 10:52:32+00:00   
22   1165267466995621888       arnoblalam 2019-08-24 14:19:48+00:00   
23   1167084630635241472        schpsych8 2019-08-29 14:40:33+00:00   
24   1165309896201527299      CodeBerry08 2019-08-24 17:08:24+00:00   
25   1167587830425690112           foe_us 2019-08-31 00:00:06+00:00   
26   1166842796331999232        CanuckPPC 2019-08-28 22:39:36+00:00   
27   1167579058777075713      Nisarmokhal 2019-08-30 23:25:14+00:00   
28   1167085586211102720      ErinHardick 2019-08-29 14:44:21+00:00   
29   1165265420217212928    MalcolmAkeem_ 2019-08-24 14:11:40+00:00   
..                   ...              ...                       ...   
170  1165226638306467840        LynnLatta 2019-08-24 11:37:34+00:00   
171  1167395382361505797         SHENERY2 2019-08-30 11:15:22+00:00   
172  1167775045743185921          ot7MbbX 2019-08-31 12:24:01+00:00   
173  1166830221741314048      ColeBrock14 2019-08-28 21:49:38+00:00   
174  1165746018526334976  DaddyKnowsBest8 2019-08-25 22:01:23+00:00   
175  1166393162396385282        enr102562 2019-08-27 16:52:55+00:00   
176  1166388156121452546      GreenFundRw 2019-08-27 16:33:01+00:00   
177  1166610094114725888    postboloneigh 2019-08-28 07:14:55+00:00   
178  1166361082405040136           TayKuj 2019-08-27 14:45:26+00:00   
179  1166529401577603072          modur_n 2019-08-28 01:54:17+00:00   
180  1167917136397815810     FirstGold_au 2019-08-31 21:48:38+00:00   
181  1167578595515977728   DrPimplePopper 2019-08-30 23:23:24+00:00   
182  1166715371799269376           KJHays 2019-08-28 14:13:15+00:00   
183  1165220207331336192          SDGsbot 2019-08-24 11:12:00+00:00   
184  1167559909308882946         alan_elj 2019-08-30 22:09:09+00:00   
185  1165636027308023814      wolfspirit1 2019-08-25 14:44:20+00:00   
186  1166558055112355840  nicole_hailee19 2019-08-28 03:48:08+00:00   
187  1166459402913816576     turkiyesever 2019-08-27 21:16:08+00:00   
188  1167574958786129920        imliberal 2019-08-30 23:08:57+00:00   
189  1165671191618543616       pegasverse 2019-08-25 17:04:03+00:00   
190  1165451238009262080       GroperBlue 2019-08-25 02:30:02+00:00   
191  1165443316122607618     KendraWrites 2019-08-25 01:58:34+00:00   
192  1167090576409280512   ToBeSafeNSound 2019-08-29 15:04:11+00:00   
193  1166631128842809345        shahjocjo 2019-08-28 08:38:30+00:00   
194  1167309093326876672    MarkKSkinner3 2019

In [17]:
writer = pd.ExcelWriter(EXCEL_FILENAME)

before_df.to_excel(writer, sheet_name = "Before")
during_df.to_excel(writer, sheet_name = "During")
after_df.to_excel(writer, sheet_name = "After")

writer.save()